In [18]:
import folium
import pandas as pd
import os
import math
import geopandas as gpd
import pandas as pd
from pprint import pprint
from ultralytics import YOLO
from tqdm import tqdm

In [3]:
df = pd.read_csv('unified_points.csv')
df

filename        distrito  \
0            TATUAPE.geojson         TATUAPE   
1            TATUAPE.geojson         TATUAPE   
2            TATUAPE.geojson         TATUAPE   
3            TATUAPE.geojson         TATUAPE   
4            TATUAPE.geojson         TATUAPE   
...                      ...             ...   
8811  JOSE BONIFACIO.geojson  JOSE BONIFACIO   
8812  JOSE BONIFACIO.geojson  JOSE BONIFACIO   
8813  JOSE BONIFACIO.geojson  JOSE BONIFACIO   
8814  JOSE BONIFACIO.geojson  JOSE BONIFACIO   
8815  JOSE BONIFACIO.geojson  JOSE BONIFACIO   

      cd_indice_vulnerabilidade_social   latitude  longitude  downloaded  \
0                                  1.0 -23.538247 -46.573478         1.0   
1                                  1.0 -23.541442 -46.569149         1.0   
2                                  2.0 -23.536791 -46.569429         1.0   
3                                  2.0 -23.531662 -46.569968         1.0   
4                                  2.0 -23.542185 -46.577823         1.0   
...                                ...        ...        ...         ...   
8811                               2.0 -23.538364 -46.436144         1.0   
8812                               2.0 -23.547568 -46.436439         1.0   
8813                               4.0 -23.543809 -46.431037         1.0   
8814                               2.0 -23.550958 -46.435750         1.0   
8815                               2.0 -23.552638 -46.437663         1.0   

                                             image_path  
0     /media/paulo/datapartition1/projects/cloudwalk...  
1     /media/paulo/datapartition1/projects/cloudwalk...  
2     /media/paulo/datapartition1/projects/cloudwalk...  
3     /media/paulo/datapartition1/projects/cloudwalk...  
4     /media/paulo/datapartition1/projects/cloudwalk...  
...                                                 ...  
8811  /media/paulo/datapartition1/projects/cloudwalk...  
8812  /media/paulo/datapartition1/projects/cloudwalk...  
8813  /media/paulo/datapartition1/projects/cloudwalk...  
8814  /media/paulo/datapartition1/projects/cloudwalk...  
8815  /media/paulo/datapartition1/projects/cloudwalk...  

[8816 rows x 7 columns]

In [5]:
model = YOLO("../models/vision/weights/best.pt")

In [6]:
conf = 0.25
iou = 0.4
images_path = './images'
ZOOM_LEVEL = 20
IMAGE_WIDTH = 640
IMAGE_HEIGHT = 640

def pixel_to_coords(bbox_x, bbox_y, center_lat, center_lon, zoom, image_width=640, image_height=640):
    """
    Converts a pixel coordinate (from top-left corner) within a satellite image tile
    to its corresponding geographical coordinate (latitude, longitude).

    Args:
        bbox_x (float): The x-coordinate of the bounding box center in pixels.
        bbox_y (float): The y-coordinate of the bounding box center in pixels.
        center_lat (float): The latitude of the center of the image tile.
        center_lon (float): The longitude of the center of the image tile.
        zoom (int): The zoom level of the map tile.
        image_width (int): The width of the image in pixels.
        image_height (int): The height of the image in pixels.

    Returns:
        tuple: A tuple containing the calculated (latitude, longitude).
    """
    # 1. Calculate the meters per pixel at the given latitude and zoom level
    # This formula is derived from the Mercator projection properties.
    meters_per_pixel = 156543.03392 * math.cos(center_lat * math.pi / 180) / (2**zoom)

    # 2. Calculate the pixel offset from the center of the image
    # The image center in pixels is (image_width / 2, image_height / 2)
    pixel_offset_x = bbox_x - image_width / 2
    # The y-axis in images goes down, while latitude goes up (north), so invert the sign.
    pixel_offset_y = image_height / 2 - bbox_y

    # 3. Convert the pixel offset to a real-world offset in meters
    meter_offset_x = pixel_offset_x * meters_per_pixel
    meter_offset_y = pixel_offset_y * meters_per_pixel

    # 4. Convert the meter offset to degrees of latitude and longitude
    # Meters per degree of latitude is roughly constant
    lat_degrees_per_meter = 1 / 111132.954
    # Meters per degree of longitude depends on the latitude
    lon_degrees_per_meter = 1 / (111320 * math.cos(center_lat * math.pi / 180))

    lat_offset_degrees = meter_offset_y * lat_degrees_per_meter
    lon_offset_degrees = meter_offset_x * lon_degrees_per_meter

    # 5. Add the offset to the center coordinates to get the final result
    final_lat = center_lat + lat_offset_degrees
    final_lon = center_lon + lon_offset_degrees

    return final_lat, final_lon

In [7]:
pool_counts = []
bbox_centers_pixels = []
bbox_centers_coords_list = []

for index, row in tqdm(df.iterrows(), total=df.shape[0], desc="Detecting Pools"):
    image_path = row['image_path']
    center_lat = row['latitude']
    center_lon = row['longitude']

    if pd.notna(image_path) and os.path.exists(image_path):
        results = model(image_path, conf=conf, iou=iou, verbose=False)

        detections = results[0].boxes

        pool_detections = detections[detections.cls == 0]

        pool_counts.append(len(pool_detections))

        current_centers_pixels = []
        current_centers_coords = []

        if len(pool_detections) > 0:
            for box in pool_detections.xywh:
                center_x, center_y = float(box[0]), float(box[1])

                current_centers_pixels.append((center_x, center_y))

                lat, lon = pixel_to_coords(
                    bbox_x=center_x,
                    bbox_y=center_y,
                    center_lat=center_lat,
                    center_lon=center_lon,
                    zoom=ZOOM_LEVEL,
                    image_width=IMAGE_WIDTH,
                    image_height=IMAGE_HEIGHT
                )
                current_centers_coords.append((lat, lon))

        bbox_centers_pixels.append(current_centers_pixels)
        bbox_centers_coords_list.append(current_centers_coords)
    else:
        pool_counts.append(0)
        bbox_centers_pixels.append([])
        bbox_centers_coords_list.append([])

df['pool_count'] = pool_counts
df['bbox_centers'] = bbox_centers_pixels
df['bbox_centers_coords'] = bbox_centers_coords_list

output_filename = "unified_points_with_detections.csv"
df.to_csv(output_filename, index=False)

print(f"\nProcessing complete.")
print(f"New DataFrame saved to '{output_filename}'")

Detecting Pools: 100%|██████████| 8816/8816 [02:19<00:00, 63.26it/s]


Processing complete.
New DataFrame saved to 'unified_points_with_detections.csv'


In [8]:
print(f'Found {sum(pool_counts)} pools')

Found 3482 pools


In [9]:
df

filename        distrito  \
0            TATUAPE.geojson         TATUAPE   
1            TATUAPE.geojson         TATUAPE   
2            TATUAPE.geojson         TATUAPE   
3            TATUAPE.geojson         TATUAPE   
4            TATUAPE.geojson         TATUAPE   
...                      ...             ...   
8811  JOSE BONIFACIO.geojson  JOSE BONIFACIO   
8812  JOSE BONIFACIO.geojson  JOSE BONIFACIO   
8813  JOSE BONIFACIO.geojson  JOSE BONIFACIO   
8814  JOSE BONIFACIO.geojson  JOSE BONIFACIO   
8815  JOSE BONIFACIO.geojson  JOSE BONIFACIO   

      cd_indice_vulnerabilidade_social   latitude  longitude  downloaded  \
0                                  1.0 -23.538247 -46.573478         1.0   
1                                  1.0 -23.541442 -46.569149         1.0   
2                                  2.0 -23.536791 -46.569429         1.0   
3                                  2.0 -23.531662 -46.569968         1.0   
4                                  2.0 -23.542185 -46.577823         1.0   
...                                ...        ...        ...         ...   
8811                               2.0 -23.538364 -46.436144         1.0   
8812                               2.0 -23.547568 -46.436439         1.0   
8813                               4.0 -23.543809 -46.431037         1.0   
8814                               2.0 -23.550958 -46.435750         1.0   
8815                               2.0 -23.552638 -46.437663         1.0   

                                             image_path  pool_count  \
0     /media/paulo/datapartition1/projects/cloudwalk...           3   
1     /media/paulo/datapartition1/projects/cloudwalk...           0   
2     /media/paulo/datapartition1/projects/cloudwalk...           0   
3     /media/paulo/datapartition1/projects/cloudwalk...           0   
4     /media/paulo/datapartition1/projects/cloudwalk...           0   
...                                                 ...         ...   
8811  /media/paulo/datapartition1/projects/cloudwalk...           1   
8812  /media/paulo/datapartition1/projects/cloudwalk...           0   
8813  /media/paulo/datapartition1/projects/cloudwalk...           0   
8814  /media/paulo/datapartition1/projects/cloudwalk...           0   
8815  /media/paulo/datapartition1/projects/cloudwalk...           0   

                                           bbox_centers  \
0     [(465.5790100097656, 413.8487243652344), (495....   
1                                                    []   
2                                                    []   
3                                                    []   
4                                                    []   
...                                                 ...   
8811           [(52.39081573486328, 613.2357177734375)]   
8812                                                 []   
8813                                                 []   
8814                                                 []   
8815                                                 []   

                                    bbox_centers_coords  
0     [(-23.53836278375694, -46.57328282451765), (-2...  
1                                                    []  
2                                                    []  
3                                                    []  
4                                                    []  
...                                                 ...  
8811       [(-23.538724737235697, -46.436503122866995)]  
8812                                                 []  
8813                                                 []  
8814                                                 []  
8815                                                 []  

[8816 rows x 10 columns]

### Calculating district area in km2

In [ ]:
gdf = gpd.read_file("limites_adm_geoportal_distrito_municipal_v2.geojson")

# The original CRS (EPSG:31983) is already projected in meters.
gdf['area_km2'] = gdf['geometry'].area / 1_000_000

district_areas = pd.DataFrame({
    'district': gdf['nm_distrito_municipal'],
    'area_km2': gdf['area_km2']
}).sort_values('district').reset_index(drop=True)

print("Area calculated from original CRS (EPSG:31983):")
print(district_areas.head())

district_areas.to_csv("district_areas_km2.csv", index=False)

Area calculated from original CRS (EPSG:31983):
            district   area_km2
0          AGUA RASA   7.175997
1  ALTO DE PINHEIROS   7.461073
2         ANHANGUERA  33.245933
3         ARICANDUVA   6.958317
4        ARTUR ALVIM   6.504243


### Estimating pool density

In [11]:
def calculate_tile_area(width_pixels, height_pixels, latitude, zoom):
    """
    Calculates the real-world area of a map tile in square kilometers.

    Args:
        width_pixels (int): The width of the tile in pixels.
        height_pixels (int): The height of the tile in pixels.
        latitude (float): The latitude for the center of the map.
        zoom (int): The zoom level of the map (1-20).

    Returns:
        float: The area of the tile in square kilometers.
    """
    # Formula to calculate meters per pixel at a given latitude and zoom level
    # This is derived from the Mercator projection used by Google Maps.
    meters_per_pixel = 156543.03392 * math.cos(latitude * math.pi / 180) / (2**zoom)

    # Calculate the width and height of the tile in meters
    width_meters = width_pixels * meters_per_pixel
    height_meters = height_pixels * meters_per_pixel

    # Calculate the area in square meters
    area_sq_meters = width_meters * height_meters

    # Convert the area to square kilometers
    area_sq_kilometers = area_sq_meters / 1_000_000

    return area_sq_kilometers

In [12]:
TILE_WIDTH, TILE_HEIGHT = 640, 640
LATITUDE = -23.56877950749253
ZOOM_LEVEL = 20

TILE_AREA = calculate_tile_area(TILE_WIDTH, TILE_HEIGHT, LATITUDE, ZOOM_LEVEL)

print(f"The area of a {TILE_WIDTH}x{TILE_HEIGHT} tile at latitude {LATITUDE} and zoom level {ZOOM_LEVEL} is approximately {TILE_AREA:.6f} km².")

The area of a 640x640 tile at latitude -23.56877950749253 and zoom level 20 is approximately 0.007670 km².


In [13]:
df_district_areas = pd.read_csv('district_areas_km2.csv')
df_district_areas

district   area_km2
0           AGUA RASA   7.175997
1   ALTO DE PINHEIROS   7.461073
2          ANHANGUERA  33.245933
3          ARICANDUVA   6.958317
4         ARTUR ALVIM   6.504243
..                ...        ...
91       VILA MARIANA   8.596830
92       VILA MATILDE   8.767290
93      VILA MEDEIROS   7.854695
94      VILA PRUDENTE   9.523903
95         VILA SONIA   9.991142

[96 rows x 2 columns]

In [14]:
districts = list(df['distrito'].unique())

district_pool_density = {}

for district in tqdm(districts):
    
    curr = {}

    district_real_area = df_district_areas[df_district_areas['district'] == district]['area_km2'].iloc[0]

    subdf = df[df['distrito'] == district]
    sample_size = len(subdf)

    pool_count = sum(subdf['pool_count'].tolist())

    total_area = sample_size * TILE_AREA

    density = pool_count / total_area
    
    curr['sample_size'] = sample_size
    curr['pool_count'] = pool_count
    curr['total_area'] = round(total_area, 2)
    curr['density'] = round(density,2)
    curr['district_real_area'] = round(float(district_real_area), 2)
    curr['total_pool_count'] = math.ceil(district_real_area * density)

    district_pool_density[district] = curr


  0%|          | 0/96 [00:00<?, ?it/s]

100%|██████████| 96/96 [00:00<00:00, 557.11it/s]


In [15]:
pprint(district_pool_density)

{'AGUA RASA': {'density': 83.45,
               'district_real_area': 7.18,
               'pool_count': 64,
               'sample_size': 100,
               'total_area': 0.77,
               'total_pool_count': 599},
 'ALTO DE PINHEIROS': {'density': 135.13,
                       'district_real_area': 7.46,
                       'pool_count': 57,
                       'sample_size': 55,
                       'total_area': 0.42,
                       'total_pool_count': 1009},
 'ANHANGUERA': {'density': 6.52,
                'district_real_area': 33.25,
                'pool_count': 5,
                'sample_size': 100,
                'total_area': 0.77,
                'total_pool_count': 217},
 'ARICANDUVA': {'density': 11.73,
                'district_real_area': 6.96,
                'pool_count': 9,
                'sample_size': 100,
                'total_area': 0.77,
                'total_pool_count': 82},
 'ARTUR ALVIM': {'density': 15.65,
                 'district_

In [68]:
pd.DataFrame.from_dict(district_pool_density, orient='index').to_csv('densities.csv')

In [16]:
total_num_pools = 0

for dist in district_pool_density:
    total_num_pools += district_pool_density[dist]['total_pool_count']

print(f'São Paulo has approximately {total_num_pools} pools!')

São Paulo has approximately 48621 pools!


### Plot

In [19]:
gdf = gpd.read_file("limites_adm_geoportal_distrito_municipal_v2.geojson")
gdf_wgs84 = gdf.to_crs(epsg=4326)

df_density = pd.DataFrame.from_dict(district_pool_density, orient='index')
df_density.reset_index(inplace=True)
df_density.rename(columns={'index': 'district'}, inplace=True)

merged_gdf = gdf_wgs84.merge(df_density, left_on='nm_distrito_municipal', right_on='district')

plot_gdf = merged_gdf[['nm_distrito_municipal', 'density', 'geometry']]

plot_gdf.rename(columns={'nm_distrito_municipal': 'district_name'}, inplace=True)

m = folium.Map(location=[-23.5505, -46.6333], zoom_start=10)

choropleth = folium.Choropleth(
    geo_data=plot_gdf,
    name='choropleth',
    data=plot_gdf,
    columns=['district_name', 'density'],
    key_on='feature.properties.district_name',
    fill_color='YlOrRd',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Pool Density (pools per km²)'
).add_to(m)

tooltip = folium.GeoJsonTooltip(
    fields=['district_name', 'density'],
    aliases=['District:', 'Pool Density:'],
    localize=True,
    sticky=False,
    style="""
        background-color: #F0EFEF;
        border: 2px solid black;
        border-radius: 3px;
        box-shadow: 3px;
    """
)
tooltip.add_to(choropleth.geojson)

# Add a layer control to the map
folium.LayerControl().add_to(m)

# Save the map to an HTML file
m.save("pool_density_map.html")

/tmp/ipykernel_114963/796986640.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  plot_gdf.rename(columns={'nm_distrito_municipal': 'district_name'}, inplace=True)


In [73]:
m